In [1]:
import pandas as pd
import numpy as np
import os, sys, json, argparse, pickle
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from generate_signals import SignalGenerator

In [2]:
self = SignalGenerator(config_name='test_0729',
                       file_net='new_sungnam_network_internal_target_0721.net.xml',
                       month=7,
                       day=29,
                       hour=9,
                       minute=40)

In [3]:
self.load_networks()

1-1. 네트워크가 로드되었습니다.


In [4]:
self.load_tables()

1-2. 테이블들이 로드되었습니다.


In [5]:
self.path_tables


'c:\\github\\siggen\\test_0729\\data\\tables'

In [6]:
# dura_As = [f'dura_A{i}' for i in range(1,9)]
# dura_Bs = [f'dura_B{i}' for i in range(1,9)]
# for i, row in self.plan.iterrows():
#     is_zero_A = (row[dura_As]==0).all()
#     is_zero_B = (row[dura_Bs]==0).all()
#     assert not (is_zero_A & is_zero_B)
#     if is_zero_B:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_B{j}'] = row[f'dura_A{j}']
#     if is_zero_A:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_A{j}'] = row[f'dura_B{j}']

In [7]:
self.prepare_auxiliaries()

1-5. 필요한 보조 객체들이 모두 준비되었습니다.


In [8]:
self.process_history()

2. 신호이력 테이블을 변환합니다.


In [14]:
print(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))

c:\github\siggen\test_0729\data\tables\TL_IF_SIGL.csv


In [98]:
time_str = '2024-07-29 9:36:32'
time_dt = datetime.strptime(time_str, '%Y-%m-%d %H:%M:%S')
print(time_dt)
time_unix = int(time_dt.timestamp())

2024-07-29 09:36:32


In [103]:
phases = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))
phases = phases.drop(columns=['FRST_REG_DT', 'RINGA_FLOW', 'RINGB_FLOW'])
phases = phases.rename(columns={
    'PHASE_DT':'start_unix','CRSRD_ID':'inter_no',
    'RINGA_PHASE':'phas_A', 'RINGB_PHASE':'phas_B',
    'MAP_MODE':'STOS_NO'
    })
isp2move_A = self.isp2move['A']
isp2move_B = self.isp2move['B']
phases['move_A'] = phases.apply(
    lambda row: int(isp2move_A.get((row.inter_no, row.STOS_NO, row.phas_A), -1)), axis=1)
phases['move_B'] = phases.apply(
    lambda row: int(isp2move_B.get((row.inter_no, row.STOS_NO, row.phas_B), -1)), axis=1)
phases['start_unix'] = phases['start_unix'].apply(lambda time_str:int(datetime.strptime(time_str, '%Y-%m-%d %H:%M:%S').timestamp()))

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0    1722213392       436       3       3        0       7       4
1    1722213392       437       4       4        0       7       4
2    1722213392       438       3       3        0       8       3
3    1722213392       442       4       4        0       7       4
4    1722213392       443       1       1        0       6       2
..          ...       ...     ...     ...      ...     ...     ...
575  1722213450       444       4       4        0      -1      -1
576  1722213450       455       1       1        0       6       2
577  1722213450       456       2       2        0       6       2
578  1722213450       457       1       1        0       6       2
579  1722213450       458       1       1        0       8       4

[580 rows x 7 columns]

In [109]:
print(phases.start_unix.min())
print(phases.start_unix.max())
print(self.present_time)

1722213392
1722213450
1722213600


In [117]:
fsec = 1722213395
move = phases[phases.start_unix <= fsec]
display(move)
recent_histories = [group.iloc[-1:] for _, group in self.history[self.history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
if not recent_histories:
    rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
else:
    rhistory = pd.concat(recent_histories)
# display(rhistory.head())
recent_unix = rhistory[['inter_no', 'end_unix']]
display(recent_unix)
move = pd.merge(move, recent_unix, how='left', on='inter_no')
display(move)
# move = move.rename(columns={'end_unix':'start_unix'})
# try:
#     movement
# except NameError:
#     movement = pd.DataFrame()
# movement = pd.concat([movement, move])
# movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
# movement = movement[movement.start_unix > fsec - self.subtractor // 2]

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0   1722213392       436       3       3        0       7       4
1   1722213392       437       4       4        0       7       4
2   1722213392       438       3       3        0       8       3
3   1722213392       442       4       4        0       7       4
4   1722213392       443       1       1        0       6       2
5   1722213392       444       3       3        0      -1      -1
6   1722213392       455       1       1        0       6       2
7   1722213392       456       4       4        0      17      -1
8   1722213392       457       5       5        0       7       4
9   1722213392       458       1       1        0       8       4
10  1722213393       436       3       3        0       7       4
11  1722213393       437       4       4        0       7       4
12  1722213393       438       3       3        0       8       3
13  1722213393       442       4       4        0       7       4
14  1722213393       443       1       1        0       6       2
15  1722213393       444       3       3        0      -1      -1
16  1722213393       455       1       1        0       6       2
17  1722213393       456       4       4        0      17      -1
18  1722213393       457       5       5        0       7       4
19  1722213393       458       1       1        0       8       4
20  1722213394       436       3       3        0       7       4
21  1722213394       437       4       4        0       7       4
22  1722213394       438       3       3        0       8       3
23  1722213394       442       4       4        0       7       4
24  1722213394       443       1       1        0       6       2
25  1722213394       444       3       3        0      -1      -1
26  1722213394       455       1       1        0       6       2
27  1722213394       456       4       4        0      17      -1
28  1722213394       457       5       5        0       7       4
29  1722213394       458       1       1        0       8       4
50  1722213395       436       3       3        0       7       4
51  1722213395       437       4       4        0       7       4
52  1722213395       438       3       3        0       8       3
53  1722213395       442       4       4        0       7       4
54  1722213395       443       1       1        0       6       2
55  1722213395       444       3       3        0      -1      -1
56  1722213395       455       1       1        0       6       2
57  1722213395       456       4       4        0      17      -1
58  1722213395       457       5       5        0       7       4
59  1722213395       458       1       1        0       8       4

inter_no    end_unix
1925       436  1722213230
1929       437  1722213270
1930       438  1722213270
1926       442  1722213240
1928       443  1722213269
1933       455  1722213350
1934       456  1722213360
1932       457  1722213309
1935       458  1722213360

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B  \
0   1722213392       436       3       3        0       7       4   
1   1722213392       437       4       4        0       7       4   
2   1722213392       438       3       3        0       8       3   
3   1722213392       442       4       4        0       7       4   
4   1722213392       443       1       1        0       6       2   
5   1722213392       444       3       3        0      -1      -1   
6   1722213392       455       1       1        0       6       2   
7   1722213392       456       4       4        0      17      -1   
8   1722213392       457       5       5        0       7       4   
9   1722213392       458       1       1        0       8       4   
10  1722213393       436       3       3        0       7       4   
11  1722213393       437       4       4        0       7       4   
12  1722213393       438       3       3        0       8       3   
13  1722213393       442       4       4        0       7       4   
14  1722213393       443       1       1        0       6       2   
15  1722213393       444       3       3        0      -1      -1   
16  1722213393       455       1       1        0       6       2   
17  1722213393       456       4       4        0      17      -1   
18  1722213393       457       5       5        0       7       4   
19  1722213393       458       1       1        0       8       4   
20  1722213394       436       3       3        0       7       4   
21  1722213394       437       4       4        0       7       4   
22  1722213394       438       3       3        0       8       3   
23  1722213394       442       4       4        0       7       4   
24  1722213394       443       1       1        0       6       2   
25  1722213394       444       3       3        0      -1      -1   
26  1722213394       455       1       1        0       6       2   
27  1722213394       456       4       4        0      17      -1   
28  1722213394       457       5       5        0       7       4   
29  1722213394       458       1       1        0       8       4   
30  1722213395       436       3       3        0       7       4   
31  1722213395       437       4       4        0       7       4   
32  1722213395       438       3       3        0       8       3   
33  1722213395       442       4       4        0       7       4   
34  1722213395       443       1       1        0       6       2   
35  1722213395       444       3       3        0      -1      -1   
36  1722213395       455       1       1        0       6       2   
37  1722213395       456       4       4        0      17      -1   
38  1722213395       457       5       5        0       7       4   
39  1722213395       458       1       1        0       8       4   

        end_unix  
0   1.722213e+09  
1   1.722213e+09  
2   1.722213e+09  
3   1.722213e+09  
4   1.722213e+09  
5            NaN  
6   1.722213e+09  
7   1.722213e+09  
8   1.722213e+09  
9   1.722213e+09  
10  1.722213e+09  
11  1.722213e+09  
12  1.722213e+09  
13  1.722213e+09  
14  1.722213e+09  
15           NaN  
16  1.722213e+09  
17  1.722213e+09  
18  1.722213e+09  
19  1.722213e+09  
20  1.722213e+09  
21  1.722213e+09  
22  1.722213e+09  
23  1.722213e+09  
24  1.722213e+09  
25           NaN  
26  1.722213e+09  
27  1.722213e+09  
28  1.722213e+09  
29  1.722213e+09  
30  1.722213e+09  
31  1.722213e+09  
32  1.722213e+09  
33  1.722213e+09  
34  1.722213e+09  
35           NaN  
36  1.722213e+09  
37  1.722213e+09  
38  1.722213e+09  
39  1.722213e+09

In [105]:
for fsec in range(self.present_time - self.sim_timespan, self.present_time + 1, 5):
    move = phases[phases.start_unix <= fsec]
    if not len(move):
        continue
    recent_histories = [group.iloc[-1:] for _, group in self.history[self.history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move = move.rename(columns={'end_unix':'start_unix'})
    try:
        movement
    except NameError:
        movement = pd.DataFrame()
    movement = pd.concat([movement, move])
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    display(movement)
    movement = movement[movement.start_unix > fsec - self.subtractor // 2]

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B  \
0   1722213392       436       3       3        0       7       4   
1   1722213392       437       4       4        0       7       4   
2   1722213392       438       3       3        0       8       3   
3   1722213392       442       4       4        0       7       4   
4   1722213392       443       1       1        0       6       2   
5   1722213392       444       3       3        0      -1      -1   
6   1722213392       455       1       1        0       6       2   
7   1722213392       456       4       4        0      17      -1   
8   1722213392       457       5       5        0       7       4   
9   1722213392       458       1       1        0       8       4   
10  1722213393       436       3       3        0       7       4   
11  1722213393       437       4       4        0       7       4   
12  1722213393       438       3       3        0       8       3   
13  1722213393       442       4       4        0       7       4   
14  1722213393       443       1       1        0       6       2   
15  1722213393       444       3       3        0      -1      -1   
16  1722213393       455       1       1        0       6       2   
17  1722213393       456       4       4        0      17      -1   
18  1722213393       457       5       5        0       7       4   
19  1722213393       458       1       1        0       8       4   
20  1722213394       436       3       3        0       7       4   
21  1722213394       437       4       4        0       7       4   
22  1722213394       438       3       3        0       8       3   
23  1722213394       442       4       4        0       7       4   
24  1722213394       443       1       1        0       6       2   
25  1722213394       444       3       3        0      -1      -1   
26  1722213394       455       1       1        0       6       2   
27  1722213394       456       4       4        0      17      -1   
28  1722213394       457       5       5        0       7       4   
29  1722213394       458       1       1        0       8       4   
30  1722213395       436       3       3        0       7       4   
31  1722213395       437       4       4        0       7       4   
32  1722213395       438       3       3        0       8       3   
33  1722213395       442       4       4        0       7       4   
34  1722213395       443       1       1        0       6       2   
35  1722213395       444       3       3        0      -1      -1   
36  1722213395       455       1       1        0       6       2   
37  1722213395       456       4       4        0      17      -1   
38  1722213395       457       5       5        0       7       4   
39  1722213395       458       1       1        0       8       4   

      start_unix  
0   1.722213e+09  
1   1.722213e+09  
2   1.722213e+09  
3   1.722213e+09  
4   1.722213e+09  
5            NaN  
6   1.722213e+09  
7   1.722213e+09  
8   1.722213e+09  
9   1.722213e+09  
10  1.722213e+09  
11  1.722213e+09  
12  1.722213e+09  
13  1.722213e+09  
14  1.722213e+09  
15           NaN  
16  1.722213e+09  
17  1.722213e+09  
18  1.722213e+09  
19  1.722213e+09  
20  1.722213e+09  
21  1.722213e+09  
22  1.722213e+09  
23  1.722213e+09  
24  1.722213e+09  
25           NaN  
26  1.722213e+09  
27  1.722213e+09  
28  1.722213e+09  
29  1.722213e+09  
30  1.722213e+09  
31  1.722213e+09  
32  1.722213e+09  
33  1.722213e+09  
34  1.722213e+09  
35           NaN  
36  1.722213e+09  
37  1.722213e+09  
38  1.722213e+09  
39  1.722213e+09

ValueError: cannot reindex on an axis with duplicate labels

In [16]:
movement

NameError: name 'movement' is not defined

In [23]:
self.process_movement()

3. 이동류정보 테이블을 변환합니다.


In [32]:
self.inter_nos

[436, 437, 438, 442, 443, 455, 456, 457, 458]

In [41]:
if heathcliff is None:
    print('heathcliff')

NameError: name 'heathcliff' is not defined

In [33]:
self.movement_updated[self.movement_updated.inter_no==436][:60]

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0    1.722246e+09       436       3       3      0.0       7       4
10   1.722246e+09       436       3       3      0.0       7       4
20   1.722246e+09       436       3       3      0.0       7       4
30   1.722246e+09       436       3       3      0.0       7       4
40   1.722246e+09       436       3       3      0.0       7       4
50   1.722246e+09       436       3       3      0.0       7       4
60   1.722246e+09       436       3       3      0.0       7       4
70   1.722246e+09       436       3       3      0.0       7       4
80   1.722246e+09       436       3       3      0.0       7       4
90   1.722246e+09       436       3       3      0.0       7       4
100  1.722246e+09       436       3       3      0.0       7       4
110  1.722246e+09       436       3       3      0.0       7       4
120  1.722246e+09       436       3       3      0.0       7       4
130  1.722246e+09       436       3       3      0.0       7       4
140  1.722246e+09       436       4       4      0.0       6       1
150  1.722246e+09       436       4       4      0.0       6       1
160  1.722246e+09       436       4       4      0.0       6       1
170  1.722246e+09       436       4       4      0.0       6       1
180  1.722246e+09       436       4       4      0.0       6       1
190  1.722246e+09       436       4       4      0.0       6       1
200  1.722246e+09       436       4       4      0.0       6       1
210  1.722246e+09       436       4       4      0.0       6       1
220  1.722246e+09       436       4       4      0.0       6       1
230  1.722246e+09       436       4       4      0.0       6       1
240  1.722246e+09       436       4       4      0.0       6       1
250  1.722246e+09       436       4       4      0.0       6       1
260  1.722246e+09       436       4       4      0.0       6       1
270  1.722246e+09       436       4       4      0.0       6       1
280  1.722246e+09       436       4       4      0.0       6       1
290  1.722246e+09       436       4       4      0.0       6       1
300  1.722246e+09       436       4       4      0.0       6       1
310  1.722246e+09       436       4       4      0.0       6       1
320  1.722246e+09       436       4       4      0.0       6       1
330  1.722246e+09       436       4       4      0.0       6       1
340  1.722246e+09       436       4       4      0.0       6       1
350  1.722246e+09       436       4       4      0.0       6       1
360  1.722246e+09       436       4       4      0.0       6       1
370  1.722246e+09       436       4       4      0.0       6       1
380  1.722246e+09       436       4       4      0.0       6       1
390  1.722246e+09       436       4       4      0.0       6       1
400  1.722246e+09       436       4       4      0.0       6       1
410  1.722246e+09       436       4       4      0.0       6       1
420  1.722246e+09       436       4       4      0.0       6       1
430  1.722246e+09       436       4       4      0.0       6       1
440  1.722246e+09       436       4       4      0.0       6       1
450  1.722246e+09       436       1       1      0.0       5       2
460  1.722246e+09       436       1       1      0.0       5       2
470  1.722246e+09       436       1       1      0.0       5       2
480  1.722246e+09       436       1       1      0.0       5       2
490  1.722246e+09       436       1       1      0.0       5       2
500  1.722246e+09       436       1       1      0.0       5       2
510  1.722246e+09       436       1       1      0.0       5       2
520  1.722246e+09       436       1       1      0.0       5       2
530  1.722246e+09       436       1       1      0.0       5       2
540  1.722246e+09       436       1       1      0.0       5       2
550  1.722246e+09       436       1       1      0.0       5       2
560  1.722246e+09       436       1       1      0.0       5       2
570  

In [26]:
self.merge_dfs()
self.movedur[:60]

inter_no    start_unix  phas_A  phas_B  move_A  move_B  duration
0        455  1.722212e+09       1       1       6       2        63
1        455  1.722212e+09       1       1       6       2        63
2        455  1.722212e+09       1       1       6       2        63
3        455  1.722212e+09       1       1       6       2        63
4        455  1.722213e+09       1       1       6       2        62
5        455  1.722213e+09       1       1       6       2        63
6        455  1.722213e+09       1       1       6       2        63
7        455  1.722213e+09       1       1       6       2        63
8        455  1.722213e+09       1       1       6       2        63
9        455  1.722213e+09       1       1       6       2        64
10       455  1.722213e+09       1       1       6       2        63
11       455  1.722213e+09       1       1       6       2        63
12       455  1.722213e+09       1       1       6       2        63
13       455  1.722213e+09       1       1       6       2        63
14       455  1.722213e+09       1       1       6       2        63
15       455  1.722213e+09       1       1       6       2        63
16       455  1.722213e+09       1       1       6       2        63
17       455  1.722213e+09       1       1       6       2        63
18       455  1.722213e+09       1       1       6       2        63
19       455  1.722214e+09       1       1       6       2        63
20       455  1.722214e+09       1       1       6       2        63
21       456  1.722212e+09       1       1       5       2        15
22       456  1.722212e+09       2       2       6       2        28
23       456  1.722212e+09       3       3       7       7        12
24       456  1.722212e+09       4       4      17      17        35
25       456  1.722213e+09       1       1       5       2        15
26       456  1.722213e+09       2       2       6       2        28
27       456  1.722213e+09       3       3       7       7        12
28       456  1.722213e+09       4       4      17      17        35
29       456  1.722213e+09       1       1       5       2        15
30       456  1.722213e+09       2       2       6       2        28
31       456  1.722213e+09       3       3       7       7        12
32       456  1.722213e+09       4       4      17      17        35
33       456  1.722213e+09       1       1       5       2        15
34       456  1.722213e+09       2       2       6       2        28
35       456  1.722213e+09       3       3       7       7        12
36       456  1.722213e+09       4       4      17      17        35
37       456  1.722213e+09       1       1       5       2        15
38       456  1.722213e+09       2       2       6       2        28
39       456  1.722213e+09       3       3       7       7        12
40       456  1.722213e+09       4       4      17      17        35
41       456  1.722213e+09       1       1       5       2        15
42       456  1.722213e+09       2       2       6       2        28
43       456  1.722213e+09       3       3       7       7        12
44       456  1.722213e+09       4       4      17      17        35
45       456  1.722213e+09       1       1       5       2        15
46       456  1.722213e+09       2       2       6       2        28
47       456  1.722213e+09       3       3       7       7        12
48       456  1.722213e+09       4       4      17      17        35
49       456  1.722213e+09       1       1       5       2        15
50       456  1.722213e+09       2       2       6       2        28
51       456  1.722213e+09       3       3       7       7        12
52       456  1.722213e+09       4       4      17      17        35
53       456  1.722213e+09       1       1       5       2        15
54       456  1.722213e+09       2       2       6       2        28
55       456  1.722213e+09       3       3       7       7        12
56       456  1.722213e+09       4       4      17      17        35
57